# Model Ensembling

1. Voting
  1. Classification: VotingClassifier
  2. Regression: VotingRegression
2. Bagging

In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
from google.colab import drive
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, r2_score, f1_score, accuracy_score, classification_report
from sklearn.metrics import roc_auc_score, log_loss
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV

drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [17]:
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.svm import SVC
from sklearn.ensemble import VotingClassifier
from sklearn.tree import DecisionTreeClassifier, plot_tree
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeRegressor, DecisionTreeClassifier

In [3]:
hr_path = '/content/gdrive/MyDrive/Datasets/human-resources-analytics/HR_comma_sep.csv'
hr = pd.read_csv(hr_path)
hr_dum = pd.get_dummies(hr, drop_first=True)
X = hr_dum.drop('left', axis = 1)
y = hr_dum['left']

X_train, X_test, y_train, y_test = train_test_split(X, y, stratify = y, train_size=0.7, random_state = 2022)

dtc = DecisionTreeClassifier(random_state = 2022)
svm = SVC(probability =True, random_state = 2022, kernel = 'linear')
da = LinearDiscriminantAnalysis()

scaler = StandardScaler()
pipe_svm = Pipeline([('STD', scaler), ('SVM', svm)])
voting = VotingClassifier([('TREE',dtc), ('SVM_P',pipe_svm), ('LDA', da)], voting = 'soft')
voting.fit(X_train, y_train)


VotingClassifier(estimators=[('TREE',
                              DecisionTreeClassifier(random_state=2022)),
                             ('SVM_P',
                              Pipeline(steps=[('STD', StandardScaler()),
                                              ('SVM',
                                               SVC(kernel='linear',
                                                   probability=True,
                                                   random_state=2022))])),
                             ('LDA', LinearDiscriminantAnalysis())],
                 voting='soft')

In [4]:
y_pred = voting.predict(X_test)
print(accuracy_score(y_test, y_pred))
y_pred_prob = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_prob))

0.9126666666666666
0.9732645075139029


In [5]:
import sklearn
sklearn.__version__

'1.0.2'

# Weighted Voting


In [6]:
voting = VotingClassifier([('TREE',dtc), ('SVM_P',pipe_svm), ('LDA', da)], voting = 'soft', weights = [5,6,3])
voting.fit(X_train, y_train)

VotingClassifier(estimators=[('TREE',
                              DecisionTreeClassifier(random_state=2022)),
                             ('SVM_P',
                              Pipeline(steps=[('STD', StandardScaler()),
                                              ('SVM',
                                               SVC(kernel='linear',
                                                   probability=True,
                                                   random_state=2022))])),
                             ('LDA', LinearDiscriminantAnalysis())],
                 voting='soft', weights=[5, 6, 3])

when we take weights aribitarily its not appropriate

we must consider the individual roc_auc for each model dtc, svm, lda 

these values will be appropriate weights for voting ensemble

In [7]:
# 1st by dtc
dtc = DecisionTreeClassifier(random_state = 2022)
dtc.fit(X_train, y_train)
y_pred_prob = dtc.predict_proba(X_test)[:,1]
roc_auc_dtc = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_dtc)


# 2nd by svm
svm = SVC(probability =True, random_state = 2022, kernel = 'linear')
scaler = StandardScaler()
pipe_svm = Pipeline([('STD', scaler), ('SVM', svm)])
pipe_svm.fit(X_train, y_train)
y_pred_prob = pipe_svm.predict_proba(X_test)[:,1]
roc_auc_svm = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_svm)

# 3rd by lda
da = LinearDiscriminantAnalysis()
da.fit(X_train, y_train)
y_pred_prob = da.predict_proba(X_test)[:,1]
roc_auc_da = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_da)

# using roc as weights
voting = VotingClassifier([('TREE',dtc), ('SVM_P',pipe_svm), ('LDA', da)], voting = 'soft', weights = [roc_auc_dtc,roc_auc_svm,roc_auc_da])

0.972023104955018
0.8052826457694968
0.8166539095467098


In [8]:
# fit and eval
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
print(accuracy_score(y_test, y_pred))
y_pred_prob = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_prob))

0.932
0.978932099718472


Using weights gives us better result with small improvement in evaluation accuracy and roc_auc_score improved

# Bankruptcy with Ensemble 
* svm radial
* logistic
* DT Classifier

In [26]:
from sklearn.ensemble import VotingRegressor

# Add Dataset
bank_path = '/content/gdrive/MyDrive/Datasets/Bankruptcy/Bankruptcy.csv'
Bankruptcy = pd.read_csv(bank_path)
X = Bankruptcy.drop(['NO','YR','D'], axis=1)
y = Bankruptcy['D']

X_train, X_test, y_train, y_test = train_test_split(X, y, stratify = y, train_size=0.7, random_state = 2022)

# 1st by svm

scaler = StandardScaler()
pipe_svm = Pipeline([('STD', scaler), ('SVM', svm)])
svm = SVC(probability =True, random_state = 2022)
pipe_svm.fit(X_train, y_train)
y_pred_prob = pipe_svm.predict_proba(X_test)[:,1]
roc_auc_svm = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_svm)

# 2nd by logisict
lr = LogisticRegression()
lr.fit(X_train, y_train)
y_pred_prob = lr.predict_proba(X_test)[:,1]
roc_auc_lr = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_lr)

# 3rd by DTC
dtc = DecisionTreeClassifier(random_state = 2022)
dtc.fit(X_train, y_train)
y_pred_prob = dtc.predict_proba(X_test)[:,1]
roc_auc_dtc = roc_auc_score(y_test, y_pred_prob)
print(roc_auc_dtc)


0.855
0.8049999999999999
0.8


/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [24]:
# without weights

# using roc as weights
voting = VotingClassifier([('SVM_P',pipe_svm), ('LR', lr),('TREE',dtc)], voting = 'soft')
# fit and eval
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
print(accuracy_score(y_test, y_pred))
y_pred_prob = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_prob))

0.775
0.8525


/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [25]:
# using roc as weights
voting = VotingClassifier([('SVM_P',pipe_svm), ('LR', lr),('TREE',dtc)], voting = 'soft', weights = [roc_auc_svm,roc_auc_lr,roc_auc_dtc])
# fit and eval
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
print(accuracy_score(y_test, y_pred))
y_pred_prob = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_prob))

0.775
0.855


/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


# Parameters Search with Voting using GridSearch CV


In [29]:
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import StratifiedKFold

voting = VotingClassifier([('SVM_P',pipe_svm), ('LR', lr),('TREE',dtc)], voting = 'soft')

voting.get_params()

{'estimators': [('SVM_P', Pipeline(steps=[('STD', StandardScaler()),
                   ('SVM', SVC(probability=True, random_state=2022))])),
  ('LR', LogisticRegression()),
  ('TREE', DecisionTreeClassifier(random_state=2022))],
 'flatten_transform': True,
 'n_jobs': None,
 'verbose': False,
 'voting': 'soft',
 'weights': None,
 'SVM_P': Pipeline(steps=[('STD', StandardScaler()),
                 ('SVM', SVC(probability=True, random_state=2022))]),
 'LR': LogisticRegression(),
 'TREE': DecisionTreeClassifier(random_state=2022),
 'SVM_P__memory': None,
 'SVM_P__steps': [('STD', StandardScaler()),
  ('SVM', SVC(probability=True, random_state=2022))],
 'SVM_P__verbose': False,
 'SVM_P__STD': StandardScaler(),
 'SVM_P__SVM': SVC(probability=True, random_state=2022),
 'SVM_P__STD__copy': True,
 'SVM_P__STD__with_mean': True,
 'SVM_P__STD__with_std': True,
 'SVM_P__SVM__C': 1.0,
 'SVM_P__SVM__break_ties': False,
 'SVM_P__SVM__cache_size': 200,
 'SVM_P__SVM__class_weight': None,
 'SVM_P__SVM

In [30]:

kfold = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 2022)
params = { 'SVM_P__SVM__C':np.linspace(0.001,5,5),
          'SVM_P__SVM__gamma':np.linspace(0.001,5,5),
          'LR__C':np.linspace(0.001,5,5),
          'TREE__max_depth':[None, 3, 5],
          'TREE__min_samples_split':[2,5,10],
          'TREE__min_samples_leaf':[1,5]}

gcv = GridSearchCV(voting, param_grid = params, cv = kfold, verbose = 2, scoring = 'roc_auc')
gcv.fit(X, y)
print(gcv.best_params_)
print(gcv.best_score_)   


Fitting 5 folds for each of 2250 candidates, totalling 11250 fits
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=0.001, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__mi

/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _che

[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.1s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2; total time=   0.0s


/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _che

[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5; total time=   0.0s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5; total time=   0.0s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=1.2507499999999998, SVM_P__SVM__C=0.001, SVM_P__SVM__gamma=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5; total time=   0.0s


...

/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _che

[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=5; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=10; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=10; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5,

/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _che


[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=10; total time=   0.1s
[CV] END LR__C=5.0, SVM_P__SVM__C=5.0, SVM_P__SVM__gamma=5.0, TREE__max_depth=5, TREE__min_samples_leaf=5, TREE__min_samples_split=10; total time=   0.1s
{'LR__C': 1.2507499999999998, 'SVM_P__SVM__C': 5.0, 'SVM_P__SVM__gamma': 0.001, 'TREE__max_depth': 3, 'TREE__min_samples_leaf': 5, 'TREE__min_samples_split': 2}
0.8974640743871515


/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.8/dist-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _che

{'LR__C': 1.2507499999999998, 'SVM_P__SVM__C': 5.0, 'SVM_P__SVM__gamma': 0.001, 'TREE__max_depth': 3, 'TREE__min_samples_leaf': 5, 'TREE__min_samples_split': 2}


0.8974640743871515